In [1]:
%matplotlib inline
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression

In [2]:
pd.options.display.max_columns = 400
pd.options.display.max_rows = 1000

In [3]:
dat = pd.read_hdf('train.h5')

In [4]:
dat.loc[:, 'id'].nunique()

1424

In [5]:
dat.loc[:, 'timestamp'].nunique()

1813

In [6]:
dat.loc[:, 'timestamp'].max()

1812

In [7]:
two_level_dat = dat.sort_values(['timestamp', 'id']).set_index(['timestamp', 'id'])

In [8]:
dat_pnl = two_level_dat.to_panel().transpose(2, 1, 0)

In [9]:
dat_pnl.shape

(1424, 1813, 109)

In [10]:
train_dat = dat_pnl.loc[:, 0:1000, :].copy()

In [11]:
val_dat = dat_pnl.loc[:, 1001:, :].copy()

In [12]:
def cod(y_truth, y_pred):
    r2 = 1 - np.sum((y_truth - y_pred)**2) / np.sum((y_truth - y_truth.mean())**2)
    return max(-1, np.sign(r2) * np.sqrt(np.abs(r2)))

In [13]:
train_dat.loc[:, :, 'price'] = (train_dat.loc[:, :, 'y'] + 1).cumprod()

In [14]:
train_dat.shape

(1424, 1001, 110)

In [15]:
train_dat_df = train_dat.transpose(2, 0, 1).to_frame()

In [16]:
train_dat_df.head()

derived_0  derived_1  derived_2  derived_3  derived_4  \
id timestamp                                                          
16 272        -0.156486   0.171735   0.435845  -0.008749  -1.895162   
   273        -0.156496   0.171752   0.435892  -0.015149  -1.895113   
   274        -0.156500   0.171759   0.435912  -0.017742  -1.895093   
   275        -0.156503   0.171765   0.435928  -0.020000  -1.895076   
   276        -0.156509   0.171775   0.435956  -0.023676  -1.895048   

              fundamental_0  fundamental_1  fundamental_2  fundamental_3  \
id timestamp                                                               
16 272            -0.239794      -0.291111      -0.652654      -0.282107   
   273            -0.225365      -0.291111      -0.656152      -0.282107   
   274            -0.219518      -0.291111      -0.657569      -0.282107   
   275            -0.214429      -0.291111      -0.658802      -0.282107   
   276            -0.206141      -0.291111      -0.660811      -0.282107   

              fundamental_5  fundamental_6  fundamental_7  fundamental_8  \
id timestamp                                                               
16 272            -0.127865      -0.929068       0.260373       0.008164   
   273            -0.127865      -0.929113       0.268115       0.008165   
   274            -0.127865      -0.929130       0.271251       0.008165   
   275            -0.127865      -0.929146       0.273982       0.008165   
   276            -0.127865      -0.929171       0.278428       0.008165   

              fundamental_9  fundamental_10  fundamental_11  fundamental_12  \
id timestamp                                                                  
16 272            -0.049947        3.759225       -0.663524       -0.023952   
   273            -0.049802        3.759225       -0.664908       -0.023952   
   274            -0.049743        3.759225       -0.665468       -0.023952   
   275            -0.049691        3.759225       -0.665956       -0.023952   
   276            -0.049608        3.759225       -0.666751       -0.023952   

              fundamental_13  fundamental_14  fundamental_15  fundamental_16  \
id timestamp                                                                   
16 272             -0.006398       -0.035727        0.588647       -0.355056   
   273             -0.006395       -0.035726        0.598660       -0.355062   
   274             -0.006394       -0.035726        0.602717       -0.355064   
   275             -0.006393       -0.035725        0.606248       -0.355066   
   276             -0.006392       -0.035725        0.611999       -0.355070   

              fundamental_17  fundamental_18  fundamental_19  fundamental_20  \
id timestamp                                                                   
16 272             -1.278671       -1.040913       -0.100661        0.411126   
   273             -1.278777       -1.049051       -0.100661        0.417690   
   274             -1.278819       -1.052348       -0.100661        0.420350   
   275             -1.278857       -1.055218       -0.100661        0.422665   
   276             -1.278917       -1.059893       -0.100661        0.426435   

              fundamental_21  fundamental_22  fundamental_23  fundamental_24  \
id timestamp                                                                   
16 272             -0.161091        0.502900        0.412909        0.943785   
   273             -0.161091        0.502884        0.412963        0.942894   
   274             -0.161091        0.502878        0.412985        0.942532   
   275             -0.161091        0.502872        0.413004        0.942218   
   276             -0.161091        0.502863        0.413036        0.941706   

              fundamental_25  fundamental_26  fundamental_27  fundamental_28  \
id timestamp                                                                   
16 272             -0.231702       -0.229724       -0

In [17]:
train_dat_df.loc[:, 'y':].describe()

y          price
count  100079.000000  100079.000000
mean        0.000257       1.097567
std         0.015248       0.402555
min        -0.086094       0.223595
25%        -0.006987       0.861564
50%         0.000034       1.027940
75%         0.007342       1.250418
max         0.093498       4.090689

In [18]:
train_dat_df.shape

(100079, 110)

In [19]:
lg = LinearRegression()

In [20]:
train_dat_df = train_dat_df.fillna(0)

In [21]:
lg.fit(train_dat_df.loc[:, 'derived_0':'technical_44'], train_dat_df.price)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=1, normalize=False)

In [22]:
val_dat_df = val_dat.transpose(2, 0, 1).to_frame()

In [23]:
val_dat_df.y.describe()

count    122961.000000
mean          0.000424
std           0.018191
min          -0.086094
25%          -0.007697
50%           0.000058
75%           0.008161
max           0.093498
Name: y, dtype: float64

In [24]:
val_dat_df.shape

(122961, 109)

In [25]:
price_pred = lg.predict(val_dat_df.loc[:, 'derived_0':'technical_44'])

In [26]:
val_dat_df.loc[:, 'price_pred'] = price_pred

In [27]:
val_dat_df.head(10)

derived_0  derived_1  derived_2  derived_3  derived_4  \
id timestamp                                                          
0  1105       -0.358335   0.033937  -0.008925   0.014504   0.140601   
   1106       -0.387752   0.013517  -0.012991   0.015320   0.133195   
   1107       -0.392891   0.009951  -0.013701   0.015462   0.131901   
   1108       -0.397364   0.006845  -0.014320   0.015586   0.130775   
   1109       -0.401258   0.004142  -0.014858   0.015694   0.129794   
   1110       -0.410169  -0.002043  -0.016090   0.015941   0.127551   
   1111       -0.412406  -0.003595  -0.016399   0.016003   0.126988   
   1112       -0.414353  -0.004947  -0.016668   0.016057   0.126498   
   1113       -0.416048  -0.006123  -0.016902   0.016104   0.126071   
   1114       -0.417523  -0.007148  -0.017106   0.016145   0.125699   

              fundamental_0  fundamental_1  fundamental_2  fundamental_3  \
id timestamp                                                               
0  1105           -0.099672       0.476878       0.175126      -0.155029   
   1106           -0.100011       0.488856       0.174786      -0.155920   
   1107           -0.100070       0.490948       0.174726      -0.156076   
   1108           -0.100121       0.492769       0.174674      -0.156211   
   1109           -0.100166       0.494355       0.174629      -0.156329   
   1110           -0.100269       0.497983       0.174526      -0.156600   
   1111           -0.100295       0.498894       0.174501      -0.156667   
   1112           -0.100317       0.499687       0.174478      -0.156726   
   1113           -0.100336       0.500377       0.174458      -0.156778   
   1114           -0.100353       0.500978       0.174441      -0.156822   

              fundamental_5  fundamental_6  fundamental_7  fundamental_8  \
id timestamp                                                               
0  1105           -0.126183      -0.038768      -0.128336       0.068770   
   1106           -0.126320      -0.052959      -0.122447       0.071302   
   1107           -0.126344      -0.055438      -0.121419       0.071745   
   1108           -0.126365      -0.057596      -0.120523       0.072130   
   1109           -0.126383      -0.059475      -0.119744       0.072465   
   1110           -0.126424      -0.063773      -0.117960       0.073232   
   1111           -0.126435      -0.064852      -0.117512       0.073425   
   1112           -0.126444      -0.065791      -0.117122       0.073593   
   1113           -0.126451      -0.066609      -0.116783       0.073738   
   1114           -0.126458      -0.067321      -0.116487       0.073866   

              fundamental_9  fundamental_10  fundamental_11  fundamental_12  \
id timestamp                                                                  
0  1105           -0.083288        0.012826        0.015408       -0.030217   
   1106           -0.085293        0.012682        0.016628       -0.030162   
   1107           -0.085643        0.012657        0.016841       -0.030152   
   1108           -0.085948        0.012635        0.017027       -0.030144   
   1109           -0.086214        0.012616        0.017188       -0.030136   
   1110           -0.086821        0.012573        0.017558       -0.030119   
   1111           -0.086974        0.012562        0.017651       -0.030115   
   1112           -0.087106        0.012552        0.017731       -0.030111   
   1113           -0.087222        0.012544        0.017802       -0.030108   
   1114           -0.087322        0.012537        0.017863       -0.030105   

              fundamental_13  fundamental_14  fundamental_15  fundamental_16  \
id timestamp                                                                   
0  1105             0.114982        0.005538        0.255530       -0.259577   
   1106             0.115000        0.003945        0.257066       -0.259746   
   1107             0.115003        0.003667        0.257335      

In [28]:
val_dat_pnl2 = val_dat_df.to_panel().transpose(1, 2, 0)

In [29]:
val_dat_pnl2.loc[:, :, 'y_pred'] = val_dat_pnl2.loc[:, :, 'price_pred'] / val_dat_pnl2.loc[:, :, 'price_pred'].shift() - 1

In [30]:
val_dat_pnl2.loc[0, :, :]

derived_0  derived_1  derived_2  derived_3  derived_4  \
timestamp                                                          
1001             NaN        NaN        NaN        NaN        NaN   
1002             NaN        NaN        NaN        NaN        NaN   
1003             NaN        NaN        NaN        NaN        NaN   
1004             NaN        NaN        NaN        NaN        NaN   
1005             NaN        NaN        NaN        NaN        NaN   
1006             NaN        NaN        NaN        NaN        NaN   
1007             NaN        NaN        NaN        NaN        NaN   
1008             NaN        NaN        NaN        NaN        NaN   
1009             NaN        NaN        NaN        NaN        NaN   
1010             NaN        NaN        NaN        NaN        NaN   
1011             NaN        NaN        NaN        NaN        NaN   
1012             NaN        NaN        NaN        NaN        NaN   
1013             NaN        NaN        NaN        NaN        NaN   
1014             NaN        NaN        NaN        NaN        NaN   
1015             NaN        NaN        NaN        NaN        NaN   
1016             NaN        NaN        NaN        NaN        NaN   
1017             NaN        NaN        NaN        NaN        NaN   
1018             NaN        NaN        NaN        NaN        NaN   
1019             NaN        NaN        NaN        NaN        NaN   
1020             NaN        NaN        NaN        NaN        NaN   
1021             NaN        NaN        NaN        NaN        NaN   
1022             NaN        NaN        NaN        NaN        NaN   
1023             NaN        NaN        NaN        NaN        NaN   
1024             NaN        NaN        NaN        NaN        NaN   
1025             NaN        NaN        NaN        NaN        NaN   
1026             NaN        NaN        NaN        NaN        NaN   
1027             NaN        NaN        NaN        NaN        NaN   
1028             NaN        NaN        NaN        NaN        NaN   
1029             NaN        NaN        NaN        NaN        NaN   
1030             NaN        NaN        NaN        NaN        NaN   
1031             NaN        NaN        NaN        NaN        NaN   
1032             NaN        NaN        NaN        NaN        NaN   
1033             NaN        NaN        NaN        NaN        NaN   
1034             NaN        NaN        NaN        NaN        NaN   
1035             NaN        NaN        NaN        NaN        NaN   
1036             NaN        NaN        NaN        NaN        NaN   
1037             NaN        NaN        NaN        NaN        NaN   
1038             NaN        NaN        NaN        NaN        NaN   
1039             NaN        NaN        NaN        NaN        NaN   
1040             NaN        NaN        NaN        NaN        NaN   
1041             NaN        NaN        NaN        NaN        NaN   
1042             NaN        NaN        NaN        NaN        NaN   
1043             NaN        NaN        NaN        NaN        NaN   
1044             NaN        NaN        NaN        NaN        NaN   
1045             NaN        NaN        NaN        NaN        NaN   
1046             NaN        NaN        NaN        NaN        NaN   
1047             NaN        NaN        NaN        NaN        NaN   
1048             NaN        NaN        NaN        NaN        NaN   
1049             NaN        NaN        NaN        NaN        NaN   
1050             NaN        NaN        NaN        NaN        NaN   
1051             NaN        NaN        NaN        NaN        NaN   
1052             NaN        NaN        NaN        NaN        NaN   
1053             NaN        NaN        NaN        NaN        NaN   
1054             NaN        NaN        NaN        NaN        NaN   
1055             NaN        NaN        NaN        NaN        NaN   
1056             NaN        NaN        NaN        NaN        NaN   
1057             NaN        NaN        NaN        NaN        NaN   

In [31]:
val_dat_df = val_dat_pnl2.transpose(2, 0, 1).to_frame()

In [32]:
val_dat_df.tail()

derived_0  derived_1  derived_2  derived_3  derived_4  \
id   timestamp                                                          
2149 1808        0.254596   0.064588  -0.034678  -1.345652  -0.037382   
     1809        0.254595   0.064622  -0.034706  -1.341776  -0.037390   
     1810        0.254594   0.064636  -0.034717  -1.340205  -0.037394   
     1811        0.254594   0.064648  -0.034726  -1.338838  -0.037396   
     1812        0.254593   0.064668  -0.034742  -1.336611  -0.037401   

                fundamental_0  fundamental_1  fundamental_2  fundamental_3  \
id   timestamp                                                               
2149 1808            0.245316       0.049130      -0.127823       0.282877   
     1809            0.244945       0.049128      -0.129151       0.282879   
     1810            0.244795       0.049127      -0.129688       0.282879   
     1811            0.244664       0.049126      -0.130157       0.282880   
     1812            0.244451       0.049125      -0.130919       0.282881   

                fundamental_5  fundamental_6  fundamental_7  fundamental_8  \
id   timestamp                                                               
2149 1808            0.398056      -0.072108      -0.131712       0.091775   
     1809            0.398053      -0.072108      -0.132777       0.091775   
     1810            0.398052      -0.072108      -0.133208       0.091776   
     1811            0.398051      -0.072108      -0.133583       0.091776   
     1812            0.398050      -0.072108      -0.134195       0.091776   

                fundamental_9  fundamental_10  fundamental_11  fundamental_12  \
id   timestamp                                                                  
2149 1808            0.211272       -0.072125       -0.094098        0.104260   
     1809            0.211543       -0.072161       -0.096018        0.104265   
     1810            0.211652       -0.072175       -0.096796        0.104267   
     1811            0.211748       -0.072188       -0.097473        0.104269   
     1812            0.211903       -0.072208       -0.098576        0.104272   

                fundamental_13  fundamental_14  fundamental_15  \
id   timestamp                                                   
2149 1808            -0.069645       -0.041865       -0.118812   
     1809            -0.069646       -0.041869       -0.119160   
     1810            -0.069647       -0.041871       -0.119301   
     1811            -0.069648       -0.041872       -0.119424   
     1812            -0.069649       -0.041875       -0.119624   

                fundamental_16  fundamental_17  fundamental_18  \
id   timestamp                                                   
2149 1808             0.650776       -0.085242       -0.157272   
     1809             0.650777       -0.085243       -0.158557   
     1810             0.650777       -0.085243       -0.159078   
     1811             0.650777       -0.085244       -0.159531   
     1812             0.650778       -0.085244       -0.160269   

                fundamental_19  fundamental_20  fundamental_21  \
id   timestamp                                                   
2149 1808             0.179089       -0.102826        0.033467   
     1809             0.179089       -0.102799        0.033376   
     1810             0.179089       -0.102788        0.033339   
     1811             0.179089       -0.102778        0.033307   
     1812             0.179089       -0.102762        0.033255   

                fundamental_22  fundamental_23  fundamental_24  \
id   timestamp                                                   
2149 1808            -0.159951       -0.000636        0.161682   
     1809            -0.159952       -0.000685        0.161366   
     1810            -0.159953       -0.000705        0.161237   
     1811            -0.159953       -0.000722        0.161126   
     1812            -0.159954       -0.000750        0.1

In [33]:
val_dat_df.loc[:, 'y_pred'].fillna(0, inplace=True)

In [35]:
cod(val_dat_df.y.values, val_dat_df.y_pred.clip(-0.1, 0.1))

-1